## 声音识别项目介绍

数据集来自 Eating Sound Collection，数据集中包含20种不同食物的咀嚼声音，赛题任务是给这些声音数据建模，准确分类。

train文件夹：完整的训练集；
train_sample文件夹：部分训练集；
test文件夹：测试集；

赛题包含的类别：


```
aloe
ice-cream
ribs
chocolate
cabbage
candied_fruits
soup
jelly
grapes
pizza
gummies
salmon
wings
burger
pickles
carrots
fries
chips
noodles
drinks
```

训练数据通过不同目录来区分不同类型的声音：
```
/content/train_sample/aloe
/content/train_sample/ice-cream
/content/train_sample/carrots

```


## 开发环境

* TensorFlow的版本：2.0 +
* keras
* sklearn
* librosa

## 下载数据




In [1]:
# 这里只下载部分训练集
!wget http://tianchi-competition.oss-cn-hangzhou.aliyuncs.com/531887/train_sample.zip
!wget http://tianchi-competition.oss-cn-hangzhou.aliyuncs.com/531887/test_a.zip


!unzip -qq train_sample.zip
!\rm train_sample.zip

!unzip -qq test_a.zip
!\rm test_a.zip

--2022-01-07 08:58:21--  http://tianchi-competition.oss-cn-hangzhou.aliyuncs.com/531887/train_sample.zip
Resolving tianchi-competition.oss-cn-hangzhou.aliyuncs.com (tianchi-competition.oss-cn-hangzhou.aliyuncs.com)... 118.31.232.194
Connecting to tianchi-competition.oss-cn-hangzhou.aliyuncs.com (tianchi-competition.oss-cn-hangzhou.aliyuncs.com)|118.31.232.194|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 540689175 (516M) [application/zip]
Saving to: ‘train_sample.zip’

train_sample.zip    100%[===================>] 515.64M  4.95MB/s    in 1m 52s  

2022-01-07 09:00:13 (4.61 MB/s) - ‘train_sample.zip’ saved [540689175/540689175]

--2022-01-07 09:00:13--  http://tianchi-competition.oss-cn-hangzhou.aliyuncs.com/531887/test_a.zip
Resolving tianchi-competition.oss-cn-hangzhou.aliyuncs.com (tianchi-competition.oss-cn-hangzhou.aliyuncs.com)... 118.31.232.194
Connecting to tianchi-competition.oss-cn-hangzhou.aliyuncs.com (tianchi-competition.oss-cn-hangzhou.aliyuncs.

In [2]:
# 安装语音处理依赖
!pip install librosa --user

In [8]:
# 基本库

import pandas as pd
import numpy as np

from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report
from sklearn.model_selection import GridSearchCV

from sklearn.preprocessing import MinMaxScaler


from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv2D, Flatten, Dense, MaxPool2D, Dropout
from tensorflow.keras.utils import to_categorical 

from sklearn.ensemble import RandomForestClassifier
from sklearn.svm import SVC


import os
import librosa
import librosa.display
import glob 


## 数据预处理

特征提取以及数据集的建立



In [4]:
feature = []
label = []
# 建立类别标签，不同类别对应不同的数字。
label_dict = {'aloe': 0, 'burger': 1, 'cabbage': 2,'candied_fruits':3, 'carrots': 4, 'chips':5,
                  'chocolate': 6, 'drinks': 7, 'fries': 8, 'grapes': 9, 'gummies': 10, 'ice-cream':11,
                  'jelly': 12, 'noodles': 13, 'pickles': 14, 'pizza': 15, 'ribs': 16, 'salmon':17,
                  'soup': 18, 'wings': 19}
# key和value对换
label_dict_inv = {v:k for k,v in label_dict.items()}

In [ ]:
from tqdm import tqdm
def extract_features(parent_dir, sub_dirs, max_file=10, file_ext="*.wav"):
    c = 0
    label, feature = [], []
    for sub_dir in sub_dirs:
        for fn in tqdm(glob.glob(os.path.join(parent_dir, sub_dir, file_ext))[:max_file]): # 遍历数据集的所有文件
            
           # segment_log_specgrams, segment_labels = [], []
            #sound_clip,sr = librosa.load(fn)
            #print(fn)
            label_name = fn.split('/')[-2]
            label.extend([label_dict[label_name]])
            # librosa读取声音wmv
            X, sample_rate = librosa.load(fn,res_type='kaiser_fast')
            mels = np.mean(librosa.feature.melspectrogram(y=X,sr=sample_rate).T,axis=0) # 计算梅尔频谱(mel spectrogram),并把它作为特征
            feature.extend([mels])
            
    return [feature, label]

In [9]:
# 自己更改目录
parent_dir = './train_sample/'
save_dir = "./"
folds = sub_dirs = np.array(['aloe','burger','cabbage','candied_fruits',
                             'carrots','chips','chocolate','drinks','fries',
                            'grapes','gummies','ice-cream','jelly','noodles','pickles',
                            'pizza','ribs','salmon','soup','wings'])

# 获取特征feature以及类别的label
temp = extract_features(parent_dir,sub_dirs,max_file=100)

100%|██████████| 35/35 [00:03<00:00,  9.46it/s]


In [10]:

temp = np.array(temp)  #(2, 1000)
data = temp.transpose()

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  """Entry point for launching an IPython kernel.


In [11]:
# 获取特征 (1000, 128)
X = np.vstack(data[:, 0])

# 获取标签 (1000, 20)
Y = np.array(data[:, 1])
print('X的特征尺寸是：',X.shape)
print('Y的特征尺寸是：',Y.shape)

X的特征尺寸是： (1000, 128)
Y的特征尺寸是： (1000,)


In [38]:
# 在Keras库中：to_categorical就是将类别向量转换为二进制（只有0和1）的矩阵类型表示
Y = to_categorical(Y)

In [13]:
'''最终数据'''
print(X.shape)
print(Y.shape)

(1000, 128)
(1000, 20)


In [14]:
# 训练集划分
X_train, X_test, Y_train, Y_test = train_test_split(X, Y, random_state = 1, stratify=Y)
print('训练集的大小',len(X_train))
print('测试集的大小',len(X_test))

训练集的大小 750
测试集的大小 250


In [15]:
X_train = X_train.reshape(-1, 16, 8, 1)
X_test = X_test.reshape(-1, 16, 8, 1)

## 搭建CNN网络¶


In [16]:
model = Sequential()

# 输入的大小
input_dim = (16, 8, 1)

model.add(Conv2D(64, (3, 3), padding = "same", activation = "tanh", input_shape = input_dim))# 卷积层
model.add(MaxPool2D(pool_size=(2, 2)))# 最大池化
model.add(Conv2D(128, (3, 3), padding = "same", activation = "tanh")) #卷积层
model.add(MaxPool2D(pool_size=(2, 2))) # 最大池化层
model.add(Dropout(0.1))
model.add(Flatten()) # 展开
model.add(Dense(1024, activation = "tanh"))
model.add(Dense(20, activation = "softmax")) # 输出层：20个units输出20个类的概率

# 编译模型，设置损失函数，优化方法以及评价标准
model.compile(optimizer = 'adam', loss = 'categorical_crossentropy', metrics = ['accuracy'])

In [17]:
model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d (Conv2D)             (None, 16, 8, 64)         640       
                                                                 
 max_pooling2d (MaxPooling2D  (None, 8, 4, 64)         0         
 )                                                               
                                                                 
 conv2d_1 (Conv2D)           (None, 8, 4, 128)         73856     
                                                                 
 max_pooling2d_1 (MaxPooling  (None, 4, 2, 128)        0         
 2D)                                                             
                                                                 
 dropout (Dropout)           (None, 4, 2, 128)         0         
                                                                 
 flatten (Flatten)           (None, 1024)              0

In [18]:
# 训练模型
model.fit(X_train, Y_train, epochs = 20, batch_size = 15, validation_data = (X_test, Y_test))

Epoch 1/20
50/50 [==============================] - 3s 33ms/step - loss: 2.8777 - accuracy: 0.1387 - val_loss: 2.6630 - val_accuracy: 0.1800
Epoch 2/20
50/50 [==============================] - 1s 27ms/step - loss: 2.5199 - accuracy: 0.2360 - val_loss: 2.4908 - val_accuracy: 0.2320
Epoch 3/20
50/50 [==============================] - 1s 26ms/step - loss: 2.2987 - accuracy: 0.2973 - val_loss: 2.4248 - val_accuracy: 0.2880
Epoch 4/20
50/50 [==============================] - 1s 26ms/step - loss: 2.0837 - accuracy: 0.3480 - val_loss: 2.3719 - val_accuracy: 0.3000
Epoch 5/20
50/50 [==============================] - 1s 25ms/step - loss: 1.9110 - accuracy: 0.4187 - val_loss: 2.4793 - val_accuracy: 0.3160
Epoch 6/20
50/50 [==============================] - 1s 25ms/step - loss: 1.7646 - accuracy: 0.4667 - val_loss: 2.3191 - val_accuracy: 0.3520
Epoch 7/20
50/50 [==============================] - 1s 26ms/step - loss: 1.5766 - accuracy: 0.5213 - val_loss: 2.4034 - val_accuracy: 0.3760
Epoch 8/20
50

In [20]:
#预测

def extract_features(test_dir, file_ext="*.wav"):
    feature = []
    for fn in tqdm(glob.glob(os.path.join(test_dir, file_ext))[:]): # 遍历数据集的所有文件
        X, sample_rate = librosa.load(fn,res_type='kaiser_fast')
        mels = np.mean(librosa.feature.melspectrogram(y=X,sr=sample_rate).T,axis=0) # 计算梅尔频谱(mel spectrogram),并把它作为特征
        feature.extend([mels])
    return feature
    

In [21]:
X_test = extract_features('./test_a/')

100%|██████████| 2000/2000 [03:14<00:00, 10.26it/s]


In [22]:
X_test = np.vstack(X_test)
predictions = model.predict(X_test.reshape(-1, 16, 8, 1))

In [23]:
preds = np.argmax(predictions, axis = 1)
preds = [label_dict_inv[x] for x in preds]

path = glob.glob('./test_a/*.wav')
result = pd.DataFrame({'name':path, 'label': preds})

result['name'] = result['name'].apply(lambda x: x.split('/')[-1])
result.to_csv('submit.csv',index=None)

In [24]:
!ls ./test_a/*.wav | wc -l

2000


In [25]:
!wc -l submit.csv

2001 submit.csv
